# Trimesh generator

In [1]:
import trimesh
from shapely.geometry import Polygon
import numpy as np

## Open Box

Box with length of 150mm, width of 100mm and bottom thickness 10 mm. Walls height: 40 mm.
Walls along length sides have thicknesses of 15 mm.
Walls along width have thicknesses of 30mm.

In [15]:
# Box parameters
depth = 100  # X-axis
width = 150  # Y-axis
bottom_thickness = 10
wall_height = 40

# Wall thicknesses
t_front = 15
t_back = 15
t_left = 30
t_right = 30

meshes = []

# Bottom plate
bottom = trimesh.creation.box(extents=(depth, width, bottom_thickness))
bottom.apply_translation([depth / 2, width / 2, bottom_thickness / 2])
meshes.append(bottom)

# Left wall
left_wall = trimesh.creation.box(extents=(t_front, width, wall_height))
left_wall.apply_translation(
    [t_front / 2, width / 2, bottom_thickness + wall_height / 2]
)
meshes.append(left_wall)

# Right wall
right_wall = trimesh.creation.box(extents=(t_back, width, wall_height))
right_wall.apply_translation(
    [depth - t_back / 2, width / 2, bottom_thickness + wall_height / 2]
)
meshes.append(right_wall)

# Front wall
front_wall = trimesh.creation.box(
    extents=(depth - t_front - t_back, t_left, wall_height)
)
front_wall.apply_translation(
    [
        t_front + (depth - t_front - t_back) / 2,
        t_left / 2,
        bottom_thickness + wall_height / 2,
    ]
)
meshes.append(front_wall)

# Back wall
back_wall = trimesh.creation.box(
    extents=(depth - t_front - t_back, t_right, wall_height)
)
back_wall.apply_translation(
    [
        t_front + (depth - t_front - t_back) / 2,
        width - t_right / 2,
        bottom_thickness + wall_height / 2,
    ]
)
meshes.append(back_wall)

# Combine into one mesh
box = trimesh.util.concatenate(meshes)
box = box.apply_transform(
    trimesh.transformations.rotation_matrix(3.14 / 2, [0, 0, 1], [0, 0, 0])
)

# # Export as STL
# print("Saved as open_box.stl")
box.export("generated/open_box.stl")
box.show()

## 10-sided Prism

In [3]:
# Parameters
n_sides = 10  # Decagon
side_length = 20.0  # Length of one side (mm)
height = 200.0  # Extrusion height (mm)

# Compute the radius of the circumcircle
angle = np.pi / n_sides
radius = side_length / (2 * np.sin(angle))

# Generate decagon vertices (CCW order)
vertices_2d = [
    (radius * np.cos(2 * np.pi * i / n_sides), radius * np.sin(2 * np.pi * i / n_sides))
    for i in range(n_sides)
]

# Create shapely polygon
base_polygon = Polygon(vertices_2d)

# Extrude into a prism
prism = trimesh.creation.extrude_polygon(base_polygon, height=height)


prism.export("generated/prism.stl")
prism.show()

## Gear

Gear wheel: inner radius 10mm, outer radius 40 mm and thickness 20mm, 6 rectangular  cogs with thickness of the gear, height of 10mm and width of 20mm. Cogs should be inserted 2mm into the gear

In [4]:
# Parameters
inner_radius = 10  # mm
outer_radius = 40  # mm
gear_thickness = 20  # mm
cog_length = 10  # mm (extends outward)
cog_width = 20  # mm
cog_inserted = 2
num_cogs = 6

# 1. Create the base gear (annular cylinder)
gear = trimesh.creation.annulus(
    r_min=inner_radius, r_max=outer_radius, height=gear_thickness
)

# 2. Create a single rectangular cog as a box
cog = trimesh.creation.box(extents=[cog_width, cog_length, gear_thickness])

# Move cog to the edge of gear:
# - shift along Y by (outer_radius + cog_length / 2)
# - center along Z
cog.apply_translation([0, outer_radius + cog_length / 2 - cog_inserted, 0])

# 3. Duplicate and rotate cogs around gear center
cogs = []
for i in range(num_cogs):
    angle_rad = i * (2 * np.pi / num_cogs)
    cog_i = cog.copy()
    rot = trimesh.transformations.rotation_matrix(angle_rad, [0, 0, 1])
    cog_i.apply_transform(rot)
    cogs.append(cog_i)

# 4. Combine gear and cogs
gear_with_cogs = trimesh.util.concatenate([gear] + cogs)

gear_with_cogs.export("generated/gear.stl")
gear_with_cogs.show()

## Tube

A tall vertical cylinder (116mm diameter, 200mm height) is partially subtracted by a smaller offset cylinder (66mm diameter, 200mm height) In the center of cylinder


In [8]:
# Dimensions
outer_diameter = 116.0  # mm
inner_diameter = 66.0  # mm
height = 200.0  # mm

# Create the outer solid cylinder
outer_cyl = trimesh.creation.cylinder(
    radius=outer_diameter / 2, height=height, sections=64
)

# Create the inner cylinder to subtract (hole)
inner_cyl = trimesh.creation.cylinder(
    radius=inner_diameter / 2, height=height, sections=64
)


tube = outer_cyl.difference(inner_cyl)
tube.export("generated/tube.stl")
tube.show()

## Ladder

The resulting object is a solid, monolithic block measuring 60 mm wide, 80 mm high, and 50 mm deep, with a two-step profile on its front face composed of 40 mm risers and 30 mm treads. The block is bisected by a full-width planar cut on its right side that connects the top-back edge to the bottom-front edge, creating a new face angled at approximately 58 degrees relative to the base. All other primary planes and unspecified corners remain mutually orthogonal at 90 degrees.

In [31]:
# Overall dimensions
width = 60.0  # Total width in mm (X-axis)
height = 80.0  # Total height in mm (Y-axis)

# Step profile dimensions
step_riser = 40.0  # Vertical height of each step
step_tread = 30.0  # Horizontal depth of each step

# --- Assumptions for Unspecified Dimensions ---
depth = 50.0  # Assumed depth in mm (Z-axis)

# --- 2. Create the Base and Stepped Geometry ---

# The origin (0,0,0) is placed at the back-bottom-left corner.
main_block = trimesh.primitives.Box(bounds=[[0, 0, 0], [width, height, depth]])

# Subtract a block from the top-front area to create the step profile.
cutout_bounds = [[0, step_riser, 0], [step_tread, height, depth]]
step_cutout = trimesh.primitives.Box(bounds=cutout_bounds)

# Perform the first boolean difference.
stepped_block = main_block.difference(step_cutout)

# This cut is a planar slice on the side of the object. We create a wedge
# by defining its profile in 2D and extruding it.

# The 2D profile lies in what will become the YZ plane of the final object.
# To do this easily, we define it in the XY plane and then rotate the result.
# In this temporary 2D plane:
#   - The X-axis represents the final object's Y-axis (height).
#   - The Y-axis represents the final object's Z-axis (depth).
p1 = [height, 0]  # Corresponds to (y=80, z=0) -> Top-Back
p2 = [0, depth]  # Corresponds to (y=0, z=50) -> Bottom-Front
p3 = [height, depth]  # Corresponds to (y=80, z=50) -> Top-Front
points_2d = np.array([p1, p2, p3])
faces_2d = np.array([[0, 1, 2]])

# Extrude this profile along the Z-axis by a length equal to the object's width.
# This creates a cutter that is oriented incorrectly.
cutter_oriented_wrong = trimesh.creation.extrude_triangulation(
    points_2d, faces_2d, height=width
)

# Now, create a transformation matrix to reorient the cutter correctly.
# We want to map the cutter's (x, y, z) coordinates to the final (x', y', z'):
#   x' = z  (The extrusion direction becomes the X-axis)
#   y' = x  (The profile's first coordinate becomes the Y-axis)
#   z' = y  (The profile's second coordinate becomes the Z-axis)
transform_matrix = np.array([[0, 0, 1, 0], [1, 0, 0, 0], [0, 1, 0, 0], [0, 0, 0, 1]])

# Apply the transformation to get the final cutting tool.
side_cutter = cutter_oriented_wrong.apply_transform(transform_matrix)
# Perform the final boolean difference.
ladder = stepped_block.difference(side_cutter)
ladder.export("generated/ladder.stl")
ladder.show()

## Spheres

Big sphere with radius 100mm, It is modified by removing the part, corresponding to the small sphere with radius 80mm and shifted from the center of big sphere 20mm up and 70mm left. Another small sphere of radius 50mm touches the bottom of big sphere

In [53]:
big_sphere_radius = 100.0
big_sphere_center = [0.0, 0.0, 0.0]

# --- Sphere for Cutting (Difference) ---
cutting_sphere_radius = 80.0
# Shifted 20mm up (+Y) and 70mm left (-X)
cutting_sphere_offset = [-70.0, 20.0, 0.0]

# --- Sphere for Adding (Union) ---
touching_sphere_radius = 50.0
# Touches the bottom of the big sphere.
# Its center will be at the big sphere's bottom point minus its own radius.
# Big sphere bottom Y = -100. New center Y = -100 - 50 = -150.
touching_sphere_center = [0.0, -big_sphere_radius - touching_sphere_radius, 0.0]

# Use a higher subdivision count for smoother spheres and more accurate booleans
sphere_subdivisions = 5

# 2. Create the initial mesh objects
print("Creating the initial sphere meshes...")

# Create the main, large sphere
big_sphere = trimesh.creation.icosphere(
    subdivisions=sphere_subdivisions, radius=big_sphere_radius
)

# Create the sphere that will be used to cut the large one
cutting_sphere = trimesh.creation.icosphere(
    subdivisions=sphere_subdivisions, radius=cutting_sphere_radius
)
cutting_sphere.apply_translation(cutting_sphere_offset)

# Create the sphere that will be added to the bottom
touching_sphere = trimesh.creation.icosphere(
    subdivisions=sphere_subdivisions, radius=touching_sphere_radius
)
touching_sphere.apply_translation(touching_sphere_center)


# 3. Perform the sequential boolean operations

# --- Step A: Difference ---
# Subtract the cutting sphere from the big sphere
print("Performing boolean difference (cut)...")
intermediate_mesh = big_sphere.difference(cutting_sphere)

# Check if the operation was successful
if intermediate_mesh.is_empty:
    raise ValueError("The difference operation failed, resulting in an empty mesh.")
else:
    print("Difference operation successful.")

# --- Step B: Union ---
# Add the touching sphere to the result of the previous operation
print("Performing boolean union (add)...")
final_mesh = intermediate_mesh.union(
    touching_sphere,
)

# Check if the final operation was successful
if final_mesh.is_empty:
    raise ValueError("The union operation failed, resulting in an empty mesh.")
else:
    print("Union operation successful. Final mesh generated.")

spheres = final_mesh
spheres.export("generated/spheres.stl")
spheres.show()

Creating the initial sphere meshes...
Performing boolean difference (cut)...
Difference operation successful.
Performing boolean union (add)...
Union operation successful. Final mesh generated.
